In [88]:
import gym
from gym import spaces
import numpy as np
import pandas as pd
pd.options.mode.chained_assignment = None 

import matplotlib.pyplot as plt
from stable_baselines3.common.env_checker import check_env
from stable_baselines3 import DQN
from env import get_dataset, Battery

from plot import display_profit, display_schedule

from sklearn.preprocessing import MinMaxScaler
from tqdm import tqdm



import plotly.express as px
import datetime


import plotly.graph_objects as go
from plotly.subplots import make_subplots

import datetime
import warnings

from scipy.optimize import linprog


# Get datasets and envs

In [89]:
import gym
from gym import spaces
import numpy as np
import pandas as pd
from tqdm import tqdm



def get_dataset(path="data/european_wholesale_electricity_price_data_hourly.csv", year="2016",country="Germany", usecols=["Datetime (UTC)", "Price (EUR/MWhe)", "Country"]):
    df = pd.read_csv(path,usecols=usecols)
    print(df)
    df = df[df.Country == country]
    df = df[df["Datetime (UTC)"] > "2020-01-01 00:00:00"]
    df.drop(["Country"], axis=1, inplace=True)
    df.rename({"Datetime (UTC)": "timestamp",
                "Price (EUR/MWhe)": "price"}, axis=1,inplace=True,errors="raise")
    df["timestamp"] = pd.to_datetime(df["timestamp"], format="%Y-%m-%dT%H:%M:%S")
    df.reset_index(drop=True, inplace=True)
    return df


class Battery(gym.Env):

    def __init__(self,  df, start=0, render_mode=None, NEC=10**5):

        self.NEC = NEC
        self.E1H = NEC/2
        self.df = df 
        self.n_hours = len(self.df)
        self.SOC = np.zeros(self.n_hours)
        self.schedule = np.zeros(self.n_hours)
        self.start = start


        # We have 3 actions, corresponding to "charge, hold, discharge"
        self.action_space = spaces.Discrete(3)



    def _get_info(self):
        df_optim = self.df.copy()
        df_optim["schedule"] = self.schedule
        df_optim["SOC"] = self.SOC * 100
        
        return df_optim.iloc[self.start:]
    

    def reset(self, seed=None, options=None):
        self.hour = self.start




    def step(self, action):
        self.hour += 1
        if action == 0:
            self.SOC[self.hour] = max(
                0,  (self.SOC[self.hour-1]*self.NEC - self.E1H) / self.NEC)

        elif action == 1:
            self.SOC[self.hour] = self.SOC[self.hour-1]

        elif action == 2:
            self.SOC[self.hour] = min(
                1,  (self.SOC[self.hour-1]*self.NEC + self.E1H) / self.NEC)
            
        self.schedule[self.hour-1] = (self.SOC[self.hour]-self.SOC[self.hour-1]) * self.NEC

        reward = None 
        
       
  

        return None, None, (self.hour == self.n_hours-1), {}




In [90]:

df = get_dataset(country="France")

frame_size = 24 * 2 * 7

df_test = df[df.timestamp.dt.year==2022].reset_index(drop=True)


test_env = Battery(df_test, start = 696)

         Country       Datetime (UTC)  Price (EUR/MWhe)
0        Austria  2015-01-01 00:00:00             17.93
1        Austria  2015-01-01 01:00:00             15.17
2        Austria  2015-01-01 02:00:00             16.38
3        Austria  2015-01-01 03:00:00             17.38
4        Austria  2015-01-01 04:00:00             16.38
...          ...                  ...               ...
1901491   Sweden  2022-12-31 19:00:00             11.57
1901492   Sweden  2022-12-31 20:00:00             14.89
1901493   Sweden  2022-12-31 21:00:00              9.94
1901494   Sweden  2022-12-31 22:00:00              4.84
1901495   Sweden  2022-12-31 23:00:00              2.01

[1901496 rows x 3 columns]


# Get optimized schedule:

In [91]:


def get_daily_policy(dataset,end, frame_size) :

      P_day = dataset.iloc[end-frame_size:end,:].groupby(dataset.timestamp.dt.hour).price.mean().to_numpy()
      n_hours = 24 

            ## (I) lhs <= rhs
      lhs_ineq1 = np.tril(np.ones((n_hours,n_hours)))
      rhs_ineq1 = np.ones(n_hours) * (test_env.NEC)

      ## (II) lhs <= rhs
      lhs_ineq2 = -np.tril(np.ones((n_hours,n_hours)))
      rhs_ineq2 = np.zeros(n_hours)

      ## (III)
      bnd = np.array([(-test_env.E1H, test_env.E1H) for i in range(n_hours)])

      rhs_ineq = np.hstack((rhs_ineq1,rhs_ineq2))
      lhs_ineq = np.vstack((lhs_ineq1,lhs_ineq2))


      # format stuff as the linprog function wants
      opt = linprog(c=P_day, A_ub=lhs_ineq, b_ub=rhs_ineq,bounds=bnd)
      t  = list(opt.x)
      # t = t[-1:]+t[:-1]

      def policy(hour, E1H) :
            return (np.array(t)/E1H +1)[hour] 
      return policy 

# Test policy on test environment 

In [92]:
import pandas as pd
pd.options.mode.chained_assignment = None 

In [93]:
obs = test_env.reset()
reward_list = []
test_env.reset()
policy = get_daily_policy(test_env.df,test_env.hour, frame_size)

for i in tqdm(range(len(test_env.df))) :
    
    
    if i % 24 == 0 and i != 0 :
        policy = get_daily_policy(test_env.df,test_env.hour, frame_size)

    hour = test_env.df.timestamp.dt.hour[test_env.hour]
    day = test_env.df.timestamp.dt.day_of_week[test_env.hour]

    action = policy(hour,test_env.E1H)
    obs, reward, done, _ = test_env.step(action)
    reward_list.append(reward)
    if done : break

df_optim = test_env._get_info()


 92%|█████████▏| 8062/8760 [00:11<00:01, 696.83it/s]


In [94]:
display_profit(df_optim)

Number of neg profit days = 1


In [95]:
display_schedule(df_optim)

In [96]:
def get_charge_cycles(df_optim):
    return (df_optim.SOC - df_optim.SOC.shift(1)).abs().sum()/200

def get_action_switches(df_optim):
    return ((df_optim.SOC - df_optim.SOC.shift(1)) != (df_optim.SOC.shift(1) - df_optim.SOC.shift(2))).sum()

In [97]:
get_charge_cycles(df_optim)

803.0

In [98]:
get_action_switches(df_optim)

3355

# LP-OPTIM

In [99]:
test_env.df

timestamp  price
0    2022-01-01 00:00:00  78.48
1    2022-01-01 01:00:00  85.16
2    2022-01-01 02:00:00  50.00
3    2022-01-01 03:00:00  37.67
4    2022-01-01 04:00:00  39.70
...                  ...    ...
8755 2022-12-31 19:00:00   7.60
8756 2022-12-31 20:00:00   3.69
8757 2022-12-31 21:00:00   1.88
8758 2022-12-31 22:00:00   0.10
8759 2022-12-31 23:00:00   0.00

[8760 rows x 2 columns]

In [100]:
obs = test_env.reset()
reward_list = []
test_env.reset()
policy = get_daily_policy(test_env.df,test_env.hour+24, 24)

for i in tqdm(range(len(test_env.df)-1)) :
    
    
    if i % 24 == 0 and i != 0 :
        policy = get_daily_policy(test_env.df,test_env.hour+24, 24)
        # print( test_env.df.timestamp[test_env.hour])
        # print([policy(i,test_env.E1H) for i in range(0,24) ])
        # print(test_env.df[test_env.hour:test_env.hour+24])
    hour = test_env.df.timestamp.dt.hour[test_env.hour]
    day = test_env.df.timestamp.dt.day_of_week[test_env.hour]

    action = policy(hour,test_env.E1H)
    obs, reward, done, _ = test_env.step(action)
    reward_list.append(reward)
    if done : break

df_optim = test_env._get_info()


 92%|█████████▏| 8062/8759 [00:10<00:00, 752.38it/s]


In [101]:
display_profit(df_optim)

Number of neg profit days = 0


In [102]:
display_schedule(df_optim)

In [103]:
get_charge_cycles(df_optim)

934.5

In [104]:
get_action_switches(df_optim)

3995